## Model with polynomial features

In [1]:
#pip install scikit-learn==0.23.2

In [2]:
#import library

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.linear_model import LinearRegression, Ridge, RidgeCV, Lasso, LassoCV, ElasticNet, ElasticNetCV
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.preprocessing import StandardScaler, OneHotEncoder, PolynomialFeatures
from sklearn import metrics

In [3]:
#Columns to be considered

num_col = {'1st Flr SF',
 'Bsmt Cond',
 'Bsmt Exposure',
 'Bsmt Qual',
 'BsmtFin SF 1',
 'Exter Cond',
 'Exter Qual',
 'Fireplaces',
 'Full Bath',
 'Garage Cars',
 'Garage Cond',
 'Garage Qual',
 'Gr Liv Area',
 'Heating QC',
 'Kitchen Qual',
 'Mas Vnr Area',
 'Open Porch SF',
 'Overall Qual',
 'Total Bsmt SF',
 'Total_area',
 'Wood Deck SF',
 'age_since_built',
 'lot_frontage_imputed'}

cat_col_total = {}'MS Zoning', 'Street', 'Lot Shape', 'Land Contour', 'Utilities',
       'Lot Config', 'Land Slope', 'Neighborhood', 'Condition 1',
       'Condition 2', 'Bldg Type', 'House Style', 'Roof Style', 'Roof Matl',
       'Exterior 1st', 'Exterior 2nd', 'Mas Vnr Type', 'Exter Qual',
       'Exter Cond', 'Foundation', 'Bsmt Qual', 'Bsmt Cond', 'Bsmt Exposure',
       'BsmtFin Type 1', 'BsmtFin Type 2', 'Heating', 'Heating QC',
       'Central Air', 'Electrical', 'Kitchen Qual', 'Functional',
       'Garage Type', 'Garage Finish', 'Garage Qual', 'Garage Cond',
       'Paved Drive', 'Sale Type'

cat_to_num = {'Exter Qual', 'Exter Cond', 'Bsmt Qual', 'Bsmt Cond',
    'Bsmt Exposure', 'Heating QC',
    'Kitchen Qual', 'Garage Qual', 'Garage Cond'}
     


cat_col = {'Bldg Type',
 'Foundation',
 'Street',
 'Central Air',
 'Electrical',
 'MS Zoning',
 'Land Contour',
 'Mas Vnr Type',
 'Heating',
 'Paved Drive'
          }

In [4]:
def cleaning_data(df):
    
    # 1. Drop most missing columns 
    df = df.drop(
    columns=['Pool QC', 'Misc Feature', 'Alley', 'Fence', 'Fireplace Qu'])

    # 2. Impute lot frontage
    from sklearn.linear_model import LinearRegression
    X_lot = df[df['Lot Frontage'] > 0][['1st Flr SF','Lot Area']]
    y_lot = df[df['Lot Frontage'] > 0]['Lot Frontage']
    lot_model = LinearRegression()
    lot_model.fit(X_lot,y_lot)
    
    lot_frontage_imputed = []
    for i in range(len(df)):
        if df.loc[i,'Lot Frontage'] > 0:
            lot_frontage_imputed.append(df.loc[i,'Lot Frontage'])
        else:
            lot_frontage_imputed.append(lot_model.predict([df.loc[i,['1st Flr SF','Lot Area']]])[0])

    df['lot_frontage_imputed'] = lot_frontage_imputed
    df = df.drop(columns = ['Lot Frontage'])
    
    #Garage Imputation

    df['Garage Yr Blt'] = df['Garage Yr Blt'].map(lambda x: x if x > 0 else 0)
    df['Garage Finish'] = df['Garage Finish'].map(lambda x: x if type(x) == str else 'NO')
    df['Garage Qual'] = df['Garage Qual'].map(lambda x: x if type(x) == str else 'NO')
    df['Garage Cond'] = df['Garage Cond'].map(lambda x: x if type(x) == str else 'NO')
    df['Garage Type'] = df['Garage Type'].map(lambda x: x if type(x) == str else 'NO')
    
    #Basement imputation
    df['Bsmt Exposure'] = df['Bsmt Exposure'].map(lambda x: x if type(x) == str else 'NO')
    df['BsmtFin Type 1'] = df['BsmtFin Type 1'].map(lambda x: x if type(x) == str else 'NO')
    df['BsmtFin Type 2'] = df['BsmtFin Type 2'].map(lambda x: x if type(x) == str else 'NO')
    df['Bsmt Cond'] = df['Bsmt Cond'].map(lambda x: x if type(x) == str else 'NO')
    df['Bsmt Qual'] = df['Bsmt Qual'].map(lambda x: x if type(x) == str else 'NO')
    
    #Mansory type and area
    df['Mas Vnr Type'] = df['Mas Vnr Type'].map(lambda x: x if type(x) == str else 'NO')
    df['Mas Vnr Area'] = df['Mas Vnr Area'].map(lambda x: x if x > 0 else 0)
    
    #Electrical Imputation
    df['Electrical'] = df['Electrical'].map(lambda x: x if type(x) == str else df['Electrical'].mode()[0])
    #Drop other observation containing Null
    df = df.dropna()
    
    return df

#Feature Engieering Function
def feat_eng(df):
    df['age_since_built'] = df['Yr Sold'] - df['Year Built']
    df['Total_area'] = df['Total Bsmt SF'] + df['1st Flr SF'] + df['2nd Flr SF']
    return df
#Converted OrdiNOl Categorical columns to Numerical 
def cat2num(df):
    for col in cat_to_num:
        df[col] = df[col].map(to_num)
    return df

#Conversion function
def to_num(val):
    if val == 'Ex':
        return 5
    elif val == 'Gd':
        return 4
    elif val == 'TA' or val == 'Av':
        return 3
    elif val == 'Fa' or val == 'Mn':
        return 2
    elif val == 'Po' or val == 'No':
        return 1
    elif val == 'NO':
        return 0



In [5]:
def prep(df, train_df):
    """
    df = DataFrame to be transformed
    train_df = cleaned training set
    """

    #OneHotEncoding
    encoder = OneHotEncoder(handle_unknown='ignore', sparse=False)
    encoder.fit(train_df[cat_col])
    df_encode = pd.DataFrame(encoder.transform(df[cat_col]),
                             columns=encoder.get_feature_names(
                                 df[cat_col].columns),
                             index=df.index)

    train_df_encode = pd.DataFrame(encoder.transform(train_df[cat_col]),
                                   columns=encoder.get_feature_names(
                                       train_df[cat_col].columns),
                                   index=train_df.index)

    #Applying Polynomial Features
    poly = PolynomialFeatures(degree=2, include_bias=False)
    df_withpoly = pd.DataFrame(
        poly.fit_transform(df[num_col]),
        columns=poly.get_feature_names(input_features=df[num_col].columns),
        index=df.index)

    train_df_withpoly = pd.DataFrame(
        poly.fit_transform(train_df[num_col]),
        columns=poly.get_feature_names(
            input_features=train_df[num_col].columns),
        index=train_df.index)

    #Merge with numerical attribute
    X_new = pd.concat([df_withpoly, df_encode], axis=1)
    X_train = pd.concat([train_df_withpoly, train_df_encode], axis=1)

    #Standardize
    ss = StandardScaler()
    ss.fit(X_train)

    X_new_scaled = ss.transform(X_new)

    return X_new


#     return X_new_scaled

# INDEX PROBLEM EXIST!

Preprocessing order
1. Cleaning
1. Feature engineering
1. cat_to_num
1. OneHotEncoding

In [6]:
train = pd.read_csv('../datasets/train.csv')
train = cleaning_data(train)
train = feat_eng(train)
train = cat2num(train)
X_train = prep(train,train)
y_train = train['SalePrice']

In [7]:
test = pd.read_csv('../datasets/test.csv')
test = cleaning_data(test)
test = feat_eng(test)
test = cat2num(test)
X_test = prep(test,train)

In [8]:
X_train

Wood Deck SF  Bsmt Exposure  Open Porch SF  Mas Vnr Area  Total Bsmt SF  \
0              0.0            1.0           44.0         289.0          725.0   
1              0.0            1.0           74.0         132.0          913.0   
2              0.0            1.0           52.0           0.0         1057.0   
3            100.0            1.0            0.0           0.0          384.0   
4              0.0            1.0           59.0           0.0          676.0   
...            ...            ...            ...           ...            ...   
2046           0.0            3.0          276.0           0.0         1884.0   
2047         158.0            1.0            0.0           0.0          861.0   
2048           0.0            1.0            0.0           0.0          896.0   
2049           0.0            1.0          189.0           0.0         1200.0   
2050         140.0            1.0           60.0           0.0          994.0   

      Garage Qual  Exter Cond  Full Bath  lot_frontage_imputed  Kitchen Qual  \
0             3.0         3.0        2.0             71.191932           4.0   
1             3.0         3.0        2.0             43.000000           4.0   
2             3.0         4.0        1.0             68.000000           4.0   
3             3.0         3.0        2.0             73.000000           3.0   
4             3.0         3.0        2.0             82.000000           3.0   
...           ...         ...        ...                   ...           ...   
2046          3.0         3.0        2.0             79.000000           4.0   
2047          3.0         3.0        1.0             70.640123           3.0   
2048          2.0         3.0        1.0             57.000000           3.0   
2049          3.0         3.0        1.0             80.000000           3.0   
2050          3.0         3.0        2.0             60.000000           4.0   

      ...  Bldg Type_2fmCon  Bldg Type_Duplex  Bldg Type_Twnhs  \
0     ...               0.0               0.0              0.0   
1     ...               0.0               0.0              0.0   
2     ...               0.0               0.0              0.0   
3     ...               0.0               0.0              0.0   
4     ...               0.0               0.0              0.0   
...   ...               ...               ...              ...   
2046  ...               0.0               0.0              0.0   
2047  ...               0.0               0.0              0.0   
2048  ...               0.0               0.0              0.0   
2049  ...               0.0               0.0              0.0   
2050  ...               0.0               0.0              0.0   

      Bldg Type_TwnhsE  Foundation_BrkTil  Foundation_CBlock  \
0                  0.0                0.0                1.0   
1                  0.0                0.0                0.0   
2                  0.0                0.0                1.0   
3                  0.0                0.0                0.0   
4                  0.0                0.0                0.0   
...                ...                ...                ...   
2046               0.0                0.0                0.0   
2047               0.0                0.0                1.0   
2048               0.0                1.0                0.0   
2049               0.0                0.0                1.0   
2050               0.0                0.0                0.0   

      Foundation_PConc  Foundation_Slab  Foundation_Stone  Foundation_Wood  
0                  0.0              0.0               0.0              0.0  
1                  1.0              0.0               0.0              0.0  
2                  0.0              0.0               0.0              0.0  
3                  1.0              0.0               0.0              0.0  
4                  1.0              0.0               0.0              0.0  
...                ...              ...         

## Model Training

### Instantiate

In [9]:
#MLR
lr = LinearRegression()

#Ridge LR
r_alphas = np.logspace(0, 5, 100)
ridge_cv = RidgeCV(alphas=r_alphas)

#Lasso LR
l_alphas = np.arange(0.001, 1, 0.0025)
lasso_cv = LassoCV(alphas=l_alphas)

#Elasticnet LR
l1_ratio = np.linspace(0, 1, 21)
enet_cv = ElasticNetCV(alphas=l_alphas, l1_ratio=l1_ratio)

### Training

In [ ]:
#MLR Fitting
lr.fit(X_train,y_train)

#RidgeLR Fitting
ridge_cv.fit(X_train,y_train)

#LassoLR Fitting
lasso_cv.fit(X_train,y_train)

#ElasticNetLR Fitting
enet_cv.fit(X_train,y_train)

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 296386465918.393, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 288017071815.58826, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 285068839241.9851, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 279159595522.237, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 279095321786.8379, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 279033767727.07965, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 277881308365.73517, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 277848353398.69116, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 277816037570.5911, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 277141741779.48267, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 277120502685.77515, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 277099524885.6086, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 276629378013.7988, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 276613654869.51605, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 276598071843.97046, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python

...

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 324287077261.432, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 324240153213.00946, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 324192964911.0941, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 322859094405.77747, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 322803055592.1595, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 322746613286.1109, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 321182993438.1242, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 321113345425.9396, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 321043061057.332, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 318946748147.0358, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 318853640704.32153, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 318759414780.5217, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3

/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 315812406598.5391, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 315674709539.78613, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_coordinate_descent.py:525: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 315534702256.36554, tolerance: 1026430467.7392805
  model = cd_fast.enet_coordinate_descent_gram(
/Users/wirachlee/opt/anaconda3/lib/python

In [ ]:
#RMSE on training set
print('Linear Regression')
print(metrics.mean_squared_error(y_train,lr.predict(X_train),squared = False),'\n')
print('Ridge Regression')
print(metrics.mean_squared_error(y_train,ridge_cv.predict(X_train),squared = False),'\n')
print('Lasso Regression')
print(metrics.mean_squared_error(y_train,lasso_cv.predict(X_train),squared = False),'\n')
print('ElasticNet Regression')
print(metrics.mean_squared_error(y_train,enet_cv.predict(X_train),squared = False),'\n')

### Cross Validation

In [ ]:
ridge = Ridge(alpha=ridge_cv.alpha_)
lasso = Lasso(alpha=lasso_cv.alpha_)
enet = ElasticNet(alpha=enet_cv.alpha_, l1_ratio=enet_cv.l1_ratio_)

#Cross Validation RMSE
lr_cv_score = cross_val_score(
    lr, X_train, y_train, scoring='neg_root_mean_squared_error',
    cv=5).mean() * -1
ridge_cv_score = cross_val_score(
    ridge, X_train, y_train, scoring='neg_root_mean_squared_error',
    cv=5).mean() * -1
lasso_cv_score = cross_val_score(
    lasso, X_train, y_train, scoring='neg_root_mean_squared_error',
    cv=5).mean() * -1
enet_cv_score = cross_val_score(
    enet, X_train, y_train, scoring='neg_root_mean_squared_error',
    cv=5).mean() * -1

In [ ]:
#Cross Validation RMSE
print('Linear Regression')
print(lr_cv_score,'\n')
print('Ridge Regression')
print(ridge_cv_score,'\n')
print('Lasso Regression')
print(lasso_cv_score,'\n')
print('ElasticNet Regression')
print(enet_cv_score,'\n')

the Best model ranked by cross validation score is ElasticNet Regression

### Making prediction and submit the result!

In [ ]:
enet.fit(X_train,y_train)
Baseline_prediction = enet.predict(X_test)
Baseline_submission = pd.DataFrame(Baseline_prediction,
                                   index=test.Id,
                                   columns=['SalePrice'])
Baseline_submission.to_csv('../Submission/Baseline_submission.csv')